In [6]:
def return_eval(pred2score, target2score, mean):
    mean2 = 2 * mean
    pred  = [p.lower() for p in pred2score]
    target = [p.lower() for p in target2score]
    o = len(set(target))

    intersect = len(set(pred[:o]).intersection(set(target)))
    budgetaccone = len(set(pred[:mean]).intersection(set(target)))/mean
    budgetacctwo = len(set(pred[:mean2]).intersection(set(target)))/mean2
    prec = intersect/len(set(pred[:o])) if len(pred) > 0 else 0.0
    rec = intersect/len(target)

    
    kmean = len(set(pred[:mean]))
    k2mean = len(set(pred[:mean2]))

    if prec==0 and rec==0:
        f1=0
    else:
        f1 = 2*prec*rec/(prec+rec)
    
    return {"P@O":100*prec, "R@O": 100*rec, "F1@O":100*f1, "B@mean": budgetaccone, "B@2mean": budgetacctwo, "#k@mean": kmean, "#k@2mean": k2mean}

def final_metric_results(preds_keyphrases, labels_keyphrases, mean):
    avg_scores = defaultdict(list)
    for pred, target in zip(preds_keyphrases, labels_keyphrases):

            all_exact_results = return_eval(pred, target, mean)
            
            for m_name, value in all_exact_results.items():
                    avg_scores[m_name].append(value)

            avg_scores["pred_kpnum"].append(len(set(pred)))
            avg_scores["gt_kpnum"].append(len(set(target)))
            
    avg_scores = {m_name: round(np.mean(values),2) for m_name, values in avg_scores.items()}

    return avg_scores
    
def generate_results(df, mean):
    
    labels_keyphrases = [p.lower().split(";") for p in df["target"]]
    preds_keyphrases = []
    for i in range(len(df)):
        # preds_keyphrases.append(post_process(df.iloc[i]["keyword"])[:k])
        preds_keyphrases.append(post_process(df.iloc[i]["keyword"]))
        
    print("@",mean) 
    return final_metric_results(preds_keyphrases, labels_keyphrases, mean)